In [1]:
import pyodbc
import configparser
import pandas as pd
import numpy as np 
from datetime import datetime, time


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\relatório_improdutivo\credenciais.ini")

# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

#gerar query
query = '''
SELECT 
    e.pdv,
    e.SKU,
    COALESCE(e.SKU_PARA, e.SKU) AS SKU_FINAL,
    coalesce(e.[ESTOQUE ATUAL],d.stock_actual) as 'ESTOQUE ATUAL',
    coalesce(e.[ESTOQUE EM TRANSITO],d.stock_intransit) as 'ESTOQUE EM TRANSITO' ,
    coalesce(e.[PEDIDO PENDENTE],d.pendingorder) as 'PEDIDO PENDENTE' , 
    d.salescurve AS Curva,
    e.CATEGORIA,
    d.dayswithoutsales AS DiasSemVenda,
    d.nextcycleprojection,
    d.secondtonextcycleprojection
FROM 
    estoque_mar e   
inner JOIN draft d
    ON d.loja_id = e.PDV 
   AND d.code = COALESCE(e.SKU_PARA, e.SKU)
'''
df0 = pd.read_sql(query, conn)



C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_10928\419701015.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df0 = pd.read_sql(query, conn)


In [2]:
df0['pdv'].value_counts()

pdv
20997     3772
20969     3723
20992     3716
20995     3304
20998     3296
          ... 
24268      935
24258      804
23156      704
910173     495
910291     495
Name: count, Length: 80, dtype: int64

In [5]:
query_vendas = '''
SELECT 
	B.PDV, 
	B.SKU,
	B.DESCRICAO,
	SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
	C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN (
    SELECT SKU, MAX(ORIGEM) AS ORIGEM
    FROM estoque_mar
    GROUP BY SKU
) e ON b.SKU = e.SKU
WHERE b.[DATA] > '2024-07-28'
GROUP BY
B.PDV, 
	B.SKU,
	B.DESCRICAO,
	C.Ciclo,
	E.ORIGEM 
'''

dfv0 = pd.read_sql(query_vendas, conn)

conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_10928\1692316838.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfv0 = pd.read_sql(query_vendas, conn)


In [6]:
df=df0

In [10]:

# 1. Agrupamento
df_agrupado = dfv0.groupby(['PDV', 'SKU', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_vendas = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_vendas.columns.name = None
df_vendas = df_vendas.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_vendas.head()


PDV   SKU                            DESCRICAO  C202411  C202412  \
0  11201  1004        FLORATTA DES COL MY BLUE 75ml      0.0      0.0   
1  11201  1005     DEM FLORATTA DES COL MY BLUE 4ml      0.0      0.0   
2  11201  1078      MATCH SRUM CAP POS QUIMICA 50ml      0.0      0.0   
3  11201  1296  PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      0.0   
4  11201  1302       PMPCK LILY DES ANTIT AER 2x75g      0.0      0.0   

   C202413  C202414  C202415  C202416  C202417  ...  C202504  C202505  \
0      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   

   C202506  C202507  C202508  C202509  C202510  C202511  C202512  C202513  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[5 rows x 23 columns]

In [ ]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [ ]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
#folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\DRAFT"   # arquivo dos drafts

# Pattern to match all CSV files
#csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
#df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


#df_draft.shape


In [ ]:


#Caminho onde estão as subpastas com os arquivos CSV
#pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
#subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

#df_list = []

# Percorre todas as subpastas
#for subpasta in subpastas:
#    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
#    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

#    for arquivo in arquivos:
#        caminho_arquivo = os.path.join(subpasta, arquivo)
#        try:
#            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
#            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
#            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
#            df_list.append(df)
#        except Exception as e:
#            print(f"Erro ao ler o arquivo {arquivo}: {e}")

#if df_list:
#    df_estoque = pd.concat(df_list, ignore_index=True)

#df_estoque['PDV'] = df_estoque['PDV'].astype(str)

#df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

#df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)'''


In [11]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202511\preço BI\TABELA DE PREÇOS (2).xlsx")

c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [12]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})
df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'SUPERVISOR'])
df_pdv = df_pdv[~df_pdv['CANAL'].isin(['MTZ','LJ'])]
df_pdv = df_pdv[df_pdv['STATUS']!= "INATIVO"]

df_pdv = df_pdv.drop(columns=['STATUS'])




In [15]:
df_pdv['MATCH'] = 1

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [ ]:
#df_estoque = df_estoque[df_estoque['Arquivo_Origem']== "EUD.csv"]

In [16]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

In [17]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "EUDORA"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)



In [18]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO   MARCA       Date  NUM_CICLO  \
2479  C202516   2025-10-29 2025-11-25       28  EUDORA 2025-10-29         16   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2479     C2025    C202518               42

In [19]:
filtered_calendario['match'] = 1

In [20]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [21]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\Downloads\Tabela-de-Promocoes_C16-1757516287454.xlsx.xlsx",skiprows=1)


In [22]:
df_tabela = df_tabela[df_tabela['Cód. Combo'].isna()]

In [23]:
df_tabela = df_tabela[[    'Ciclo',                 'Veiculo',
              'Tipo de Promoção',  'Estratégia de Promoção',
                 'Tipo_mecanica', 'Promo Período Limitado?',
                           'EAM',               'Categoria',
                    'Cód. Combo',          'Código do Item',
             'Descrição do Item',     'Chamada Promocional',
                 'Valor do Guia',      'Preço Promocionado',
                 '% de Desconto',           'RE compra por',
                  'RE Vende por',          'RE lucra  (R$)']]

In [24]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype(str).str.replace(".0","",regex=False)

In [25]:
df_tabela.head()

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202516    Guia CF               BW             Escoamento  Desconto Direto   
1  202516    Guia CF               BW        Movimentar Flow  Desconto Direto   
2  202516    Guia CF               BW        Movimentar Flow  Desconto Direto   
3  202516    Guia CF               BW      Potencializa C.II  Desconto Direto   
4  202516  Fora Guia               BW             Escoamento  Desconto Direto   

  Promo Período Limitado?  EAM  Categoria  Cód. Combo Código do Item  \
0                     NaN  Sim  MAQUIAGEM         NaN          54511   
1                     NaN  Sim  MAQUIAGEM         NaN          52583   
2                     NaN  Sim  MAQUIAGEM         NaN          52584   
3                     NaN  Sim  MAQUIAGEM         NaN          54506   
4  SUPER BW - 28/11-31/11  Não      ROSTO         NaN          52166   

                                   Descrição do Item  \
0  NIINA SECRETS DELINEADOR CRYSTAL BRILHO ROSE G...   
1                NIINA SECRETS HIDRA BALM VINHO 3,2g   
2                 NIINA SECRETS HIDRA BALM ROSA 3,2g   
3               NIINA SECRETS PRIMER HIDRA GLOW 15ml   
4  EUDORA NEO DERMO ACTIVE PRO SÉRUM DUPLA VITAMI...   

                                 Chamada Promocional  Valor do Guia  \
0  BW GUIA CF| NIINA SECRETS DELINEADOR CRYSTAL B...          67.99   
1  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
2  BW | NIINA SECRETS HIDRA BALM ROSA 3,2g | DE R...          39.99   
3  BW | NIINA SECRETS PRIMER HIDRA GLOW 15ml | DE...          79.99   
4  FG CF | Super BW 28 a 31/nov EUDORA NEO DERMO ...         119.99   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0                24.9          0.634          17.43          24.9   
1                14.9          0.627          10.43          14.9   
2                14.9          0.627          10.43          14.9   
3                29.9          0.626          20.93          29.9   
4                49.9          0.584          34.93          49.9   

   RE lucra  (R$)  
0            7.47  
1            4.47  
2            4.47  
3            8.97  
4           14.97

In [26]:
df_tabela = pd.merge(left=df_tabela,right=df0[['SKU','SKU_FINAL']],left_on='Código do Item',right_on='SKU',how='inner')
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
1  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
2  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
3  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
4  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM  Categoria  Cód. Combo Código do Item  \
0                     NaN  Sim  MAQUIAGEM         NaN          52583   
1                     NaN  Sim  MAQUIAGEM         NaN          52583   
2                     NaN  Sim  MAQUIAGEM         NaN          52583   
3                     NaN  Sim  MAQUIAGEM         NaN          52583   
4                     NaN  Sim  MAQUIAGEM         NaN          52583   

                     Descrição do Item  \
0  NIINA SECRETS HIDRA BALM VINHO 3,2g   
1  NIINA SECRETS HIDRA BALM VINHO 3,2g   
2  NIINA SECRETS HIDRA BALM VINHO 3,2g   
3  NIINA SECRETS HIDRA BALM VINHO 3,2g   
4  NIINA SECRETS HIDRA BALM VINHO 3,2g   

                                 Chamada Promocional  Valor do Guia  \
0  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
1  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
2  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
3  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
4  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0                14.9          0.627          10.43          14.9   
1                14.9          0.627          10.43          14.9   
2                14.9          0.627          10.43          14.9   
3                14.9          0.627          10.43          14.9   
4                14.9          0.627          10.43          14.9   

   RE lucra  (R$)    SKU SKU_FINAL  
0            4.47  52583     52583  
1            4.47  52583     52583  
2            4.47  52583     52583  
3            4.47  52583     52583  
4            4.47  52583     52583

In [27]:
df_tabela['Código do Item'] = np.where(df_tabela['SKU_FINAL'].notna(),df_tabela['SKU_FINAL'],df_tabela['Código do Item'])

In [28]:
df_tabela = df_tabela.drop(columns=['SKU','SKU_FINAL'])

In [29]:
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
1  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
2  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
3  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   
4  202516  Guia CF               BW        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM  Categoria  Cód. Combo Código do Item  \
0                     NaN  Sim  MAQUIAGEM         NaN          52583   
1                     NaN  Sim  MAQUIAGEM         NaN          52583   
2                     NaN  Sim  MAQUIAGEM         NaN          52583   
3                     NaN  Sim  MAQUIAGEM         NaN          52583   
4                     NaN  Sim  MAQUIAGEM         NaN          52583   

                     Descrição do Item  \
0  NIINA SECRETS HIDRA BALM VINHO 3,2g   
1  NIINA SECRETS HIDRA BALM VINHO 3,2g   
2  NIINA SECRETS HIDRA BALM VINHO 3,2g   
3  NIINA SECRETS HIDRA BALM VINHO 3,2g   
4  NIINA SECRETS HIDRA BALM VINHO 3,2g   

                                 Chamada Promocional  Valor do Guia  \
0  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
1  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
2  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
3  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   
4  BW | NIINA SECRETS HIDRA BALM VINHO 3,2g | DE ...          39.99   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0                14.9          0.627          10.43          14.9   
1                14.9          0.627          10.43          14.9   
2                14.9          0.627          10.43          14.9   
3                14.9          0.627          10.43          14.9   
4                14.9          0.627          10.43          14.9   

   RE lucra  (R$)  
0            4.47  
1            4.47  
2            4.47  
3            4.47  
4            4.47

In [ ]:
df_tabela['MATCH'] = 1

In [ ]:
df_tabela = pd.merge(left=df_tabela,right=df_pdv[['PDV','MATCH','UF','DESCRIÇÃO PDV','ANALISTA']],on='MATCH',how='inner')

In [ ]:
df_tabela.head()

In [ ]:
df_tabela = df_tabela.drop_duplicates()

In [ ]:
df_tabela.columns

In [ ]:
df.columns

In [ ]:
df.head()

In [ ]:
df['pdv'] = df['pdv'].astype(str)

In [ ]:
df['SKU_FINAL'] = df['SKU_FINAL'].astype(str)


In [ ]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype('str')

In [ ]:
df_tabela.columns

In [ ]:
df_tabela['PDV'] = df_tabela['PDV'].astype(str)

In [ ]:
df[['SKU_FINAL','pdv']].head()

In [ ]:
df[(df['SKU_FINAL']=='93403')]

In [ ]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU_FINAL','pdv'],how='inner')
df_final.shape  

In [ ]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU','pdv'],how='inner')

In [ ]:
df_final.columns

In [ ]:
df_final['pdv'] = df_final['PDV']
df_final['SKU_FINAL'] = df_final['Código do Item']

In [ ]:
df_final['Descrição do Item']

In [ ]:
df_final.head(20)

In [ ]:
df_final['match'] = 1

In [ ]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], on='match',how='inner')
df_final.shape

In [ ]:
df_final.PDV.value_counts()

In [ ]:
#df_final = pd.merge(left=df_final,right=df_pdv[['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC','UF', 'MARCA', 'ANALISTA']],on = 'PDV',how='inner')
df_final.shape

In [ ]:
#df_final['SKU'] = df_final['SKU'].astype(str) 
#df_final['PDV'] = df_final['PDV'].astype(str) 
#df_final = pd.merge(left=df_final,right=df_estoque[['SKU_FINAL', 'DDV PREVISTO', 'COBERTURA ATUAL','PDV']],right_on=['PDV','SKU_FINAL'],left_on=['PDV','SKU'],how='left')
#df_final.shape

In [ ]:

r'''df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU_FINAL'],how='left')
df_final.shape  ''' 

In [ ]:
df_final['pdv'].value_counts()

In [ ]:
#df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

#df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','SKU'],how='left')
#df_final.shape   

In [ ]:
#df_bi_preco = df_bi_preco[df_bi_preco['MARCA']=='EUDORA']

In [ ]:
#df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

#df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [ ]:
#df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})
#df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

In [ ]:
df_final.columns

In [ ]:
#df_final = df_final.drop(columns=['Desativação','Lançamento','Promoção Próximo Ciclo','Compra inteligente semanal/Sugestão de compra','Planograma','Carteira Bloqueada Para Novos Pedidos','Preço Sell In','Quantidade','Item analisado','Promoção Próximo Ciclo + 1','SKU_PARA_VALIDACAO','Ciclo_y'])

In [ ]:
df_final['PDV_SKU'] = df_final['PDV'].astype(str) + df_final['SKU_FINAL'].astype(str) 
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU_FINAL'].astype(str)

df_final.shape

In [ ]:
df_final['PDV']

In [ ]:
df_final['nextcycleprojection'].value_counts()

df_final['secondtonextcycleprojection'].value_counts()

In [ ]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [ ]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'].value_counts()

In [ ]:
#df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [ ]:
df_final = df_final.rename(columns={'Arquivo_Origem': 'MARCA'})

In [ ]:
#df_final = df_final[~df_final['MARCA'].isna()]
#df_final['MARCA'].isna().sum()

In [ ]:
df_final = df_final.drop_duplicates()
df_final.shape

In [ ]:
df_final.columns

In [ ]:
df_vendas['PDV'] = df_vendas['PDV'].astype(str)
df_vendas['SKU'] = df_vendas['SKU'].astype(str)

df_vendas.columns

In [ ]:
df_final.shape

In [ ]:
df_vendas.head()

In [ ]:
df_final = pd.merge(df_final,df_vendas,left_on=['PDV','SKU'],right_on=['PDV','SKU'],how='left')

In [ ]:
df_final.columns

In [ ]:
df_final.iloc[:, -18:-1] = df_final.iloc[:, -18:-1].fillna(0)

In [ ]:
# Define list of target columns
sales_2024_cols = df_final.columns[-18:-1]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 17CICLOS'] = df_final[sales_2024_cols].max(axis=1)



In [ ]:
df_final.head()

In [ ]:
df_final.PDV.value_counts()

In [ ]:
sales_2024_cols

In [ ]:
vendas_6_meses = df_final.columns[-8:-2]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [ ]:
df_final.columns[-19]

In [ ]:
CRESCIMENTO = (df_final[df_final.columns[-18]].sum() - df_final[df_final.columns[-3]].sum())/df_final[df_final.columns[-18]].sum() 
print(CRESCIMENTO)

df_final['CRESCIMENTO'] = .2

In [ ]:
df_final.columns[-18:-17].str.split(" ")[0][-1]

In [ ]:
mesmo_ciclo_ano_passado = df_final.columns[-18]
ciclo_ano_passado = df_final.columns[-18:-17].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [ ]:
df_final.columns[-19:-3]

In [ ]:
vendas_todos_historicos = df_final.columns[-19:-3]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO'] <1,df_final['MEDIA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'])


In [ ]:
CRESCIMENTO

In [ ]:
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] < df_final['MEDIANA DO HISTÓRICO'],
                                    np.ceil(df_final['CRESCIMENTO'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO']), 
                                    np.ceil(df_final['CRESCIMENTO']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado]))

In [ ]:
#df_final['PV GINSENG'] = np.where(df_final['PV GINSENG']<1, df_final['Projeção Próximo Ciclo + 1'],df_final['PV GINSENG'])

In [ ]:
df_final.columns

In [ ]:
df_final.columns[50:59]

In [ ]:
df_final = df_final.rename(columns={df_final.columns[59]: "C-4", df_final.columns[60]: "C-3",df_final.columns[61]: "C-2",df_final.columns[62]: "C-1"})

In [ ]:
df_final.drop(columns=df_final.columns[43:48], inplace=True)

df_final.columns

In [ ]:
df_final.columns[44:54]

In [ ]:
df_final.drop(columns=df_final.columns[44:54], inplace=True)

df_final.columns

In [ ]:
df_final.columns

In [ ]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = df_final
   

In [ ]:
#df_final['Compra inteligente Próximo Ciclo']


In [ ]:
#df_final['DDV PREVISTO'] = df_final['DDV PREVISTO'].fillna(0.01)


In [ ]:
#df_final_dedup['DDV PREVISTO'] = np.where(
#    df_final_dedup['DDV PREVISTO'] == 0,
#    0.01,
#    df_final_dedup['DDV PREVISTO']
#)


In [ ]:
#df_final_dedup['DDV PREVISTO'].value_counts()

In [ ]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [ ]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [ ]:
#df_final_dedup.columns

In [ ]:
#df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [ ]:
#df_final_dedup = df_final_dedup.rename(columns={'Ciclo_x':'Ciclo'})

In [ ]:
df_final_dedup['SUGESTÃO ABASTECIMENTO'] = ''
df_final_dedup['VENDAS R$ ABASTECIMENTO'] = ''


In [ ]:
#df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [ ]:
#df_final_dedup['COB PROJETADA'] = np.where(
#    df_final_dedup['DDV PREVISTO'] != 0,
#    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
#    999)


In [ ]:
#df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL','Projeção Próximo Ciclo + 1',
#                             'CRESCIMENTO'],inplace=True)

In [ ]:
#df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [ ]:
#df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [ ]:
#df_final_dedup.columns

In [ ]:
#marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
#marca_promo

In [ ]:
df_final.columns

In [ ]:
# Passo 1: ordenar
df_sorted = df_final.sort_values(by='% de Desconto', ascending=False)

# Passo 2: obter até 3 chamadas promocionais por grupo
promo_grouped = (
    df_sorted.groupby(['SKU_FINAL', 'PDV'])['Chamada Promocional']
    .apply(lambda x: x.dropna().unique()[:3])
    .apply(pd.Series)
    .rename(columns={0: 'MECÂNICA 1', 1: 'MECÂNICA 2', 2: 'MECÂNICA 3'})
    .reset_index()
)

# Passo 3: base com maior % de desconto
df_base = df_sorted.drop_duplicates(subset=['SKU_FINAL', 'PDV'], keep='first').reset_index(drop=True)

# Passo 4: merge com chamadas pivotadas
df_merged = df_base.merge(promo_grouped, on=['SKU_FINAL', 'PDV'], how='left')

# Corrigir dicionário: agrupar e pegar o primeiro valor válido por (SKU_FINAL, PDV)
# Passo 1: dicionário com Cód. Combo único por SKU_FINAL+PDV
cod_combo_map = (
    df_final
    .dropna(subset=['Cód. Combo'])
    .groupby(['SKU_FINAL', 'PDV'])['Cód. Combo']
    .first()
    .to_dict()
)

# Passo 2: gerar Series com os valores mapeados
cod_combo_series = df_merged.set_index(['SKU_FINAL', 'pdv']).index.map(cod_combo_map)

# Passo 3: substituir os valores diretamente
df_merged['Cód. Combo'] = cod_combo_series.where(cod_combo_series.notna(), df_merged['Cód. Combo'])



In [ ]:
df_merged.PDV.value_counts()

# Columns to bring up front
priority_cols = [
    'PDV_SKU',	'SKU',	'MARCA','INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO','dias_ate_inicio',	
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição','MECÂNICA 1',
       'MECÂNICA 2', 'MECÂNICA 3','Estoque Atual',	'COBERTURA ATUAL',
    'Estoque em Transito',	'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_merged.columns if col not in priority_cols]

# Reorder
df_merged = df_merged[priority_cols + other_cols]


In [ ]:
df_merged['INICIO CICLO'] = pd.to_datetime(df_merged['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_merged['FIM CICLO'] = pd.to_datetime(df_merged['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [ ]:
df_merged.columns

In [ ]:
df_merged = df_merged.loc[:, ~df_merged.columns.str.endswith('_y')]


In [ ]:
df_merged.columns = df_merged.columns.str.replace('_x$', '', regex=True)


In [ ]:
df_merged['DESCRICAO'] = df_merged['Descrição do Item']

In [ ]:
df_merged['SKU'] = np.where(df_merged['SKU'].isna(),df_merged['SKU_FINAL'],df_merged['SKU'])

In [ ]:
df_merged = df_merged.drop(columns=['Veiculo',	'Tipo de Promoção',	'Estratégia de Promoção','Tipo_mecanica'
                                    ,'Chamada Promocional','MATCH','match','Descrição do Item','CRESCIMENTO',
                                    'Cód. Combo'])

In [ ]:
df_merged = df_merged.drop(columns=['Código do Item','PDV','RE compra por',	'RE Vende por',	'RE lucra  (R$)','INICIO CICLO',
                                    'FIM CICLO','Ciclo','CATEGORIA','ANALISTA','dias_ate_inicio','PDV_SKU','UFPRODUTO',
                                    'VENDAS R$ ABASTECIMENTO','DURAÇÃO','MEDIANA DO HISTÓRICO','DURAÇÃO'])

In [ ]:
df_merged = df_merged.rename(columns={'nextcycleprojection':'PROJEÇÃO PROX CICLO'	,'secondtonextcycleprojection':'PROJEÇÃO PROX CICLO +1'})

In [ ]:
df_merged.columns = df_merged.columns.str.upper()

In [ ]:
#df_merged = df_merged[['UF','PDV','DESCRIÇÃO PDV','SKU','DESCRICAO','EAM','CATEGORIA','CURVA','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DIASSEMVENDA','PROJEÇÃO PROX CICLO','PROJEÇÃO PROX CICLO +1','PROMO PERÍODO LIMITADO?','VALOR DO GUIA','PREÇO PROMOCIONADO','% DE DESCONTO','PICO DE VENDAS 17CICLOS','PICO VENDAS ULTIMOS 6 CICLOS','MEDIA DO HISTÓRICO']]

In [ ]:
df_merged['MEDIA DO HISTÓRICO'] = round(df_merged['MEDIA DO HISTÓRICO'],0)

In [ ]:
df_merged[df_merged.columns[19:26]] = df_merged[df_merged.columns[19:26]].fillna(0)

In [ ]:
df_merged.columns

In [ ]:
# Colunas que devem estar na frente
colunas_inicio = [
    'UF', 'PDV', 'DESCRIÇÃO PDV', 'SKU', 'DESCRICAO', 'EAM', 'CATEGORIA', 'CURVA',
    'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DIASSEMVENDA',
    'PROJEÇÃO PROX CICLO', 'PROJEÇÃO PROX CICLO +1', 'PROMO PERÍODO LIMITADO?',
    'VALOR DO GUIA', 'PREÇO PROMOCIONADO', '% DE DESCONTO',
    'PICO DE VENDAS 17CICLOS', 'PICO VENDAS ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO'
]

# Colunas que devem estar no fim
colunas_fim = [
    'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t'
]

# Todas as outras colunas (não estão nem no início nem no fim)
colunas_meio = [col for col in df_merged.columns if col not in colunas_inicio + colunas_fim]

# Reordena o DataFrame
df_merged = df_merged[colunas_inicio + colunas_meio + colunas_fim]


In [ ]:
df_merged = df_merged.drop_duplicates()

In [ ]:
hoje=datetime.today().strftime('%Y-%m-%d')
hoje

In [ ]:
df_merged = df_merged.drop(columns='SKU_FINAL')

In [ ]:

from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font


# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\EUD_promoção_{ciclo_mais2}_{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_merged.to_excel(writer, index=False, sheet_name='Sheet1')

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL